In [10]:
import sqlite3
import os
import pandas as pd
import json

In [11]:
#script_directory = os.path.dirname(os.path.abspath(__file__))
script_directory = os.path.dirname(os.getcwd())
print(script_directory)
db = []
db.append(os.path.join(script_directory, "Weather_db_20200118.db"))
db.append(os.path.join(script_directory, "Weather_db_20200621.db"))

C:\#Pyth\Sql


In [12]:
def readDB(db):
    global conn, cursor, forecasts, fnames, conditions, cnames
    conn = sqlite3.connect(db)    # všude je potřeba testovat exceptions
    conn.row_factory = sqlite3.Row          # abych mohl používat názvy sloupců místo indexů
    cursor = conn.cursor()
    cursor.execute("SELECT * " \
                   " FROM forecast")
                   #" WHERE t._id = (SELECT max(t2._id) FROM forecast t2 WHERE t2.date= t.date and t.creatat >= date('now','-1 day'))")
    forecasts = cursor.fetchall()         # načte všechnyřádky ze selectu
    fnames = list(map(lambda x: x[0], cursor.description))
    #print(cursor.description)

    cursor.execute("SELECT * FROM condition")
                   #" WHERE t._id = (SELECT max(t2._id) FROM forecast t2 WHERE t2.date= t.date and t.creatat >= date('now','-1 day'))")
    conditions = cursor.fetchall()         # načte všechnyřádky ze selectu
    cnames = list(map(lambda x: x[0], cursor.description))

    conn.close()  # toto by se mělo vždy udělat, při update načíst dtb znovu
    # pro jednoduchost zakomentováno

In [13]:
readDB(db[1])

In [14]:
print(fnames)
print(cnames)

print('Pocet forecasts:', len(forecasts))
print('Pocet conditions:', len(conditions))

for row in forecasts[:1]:
    for col in row:
        print(col)

forecasts_df = pd.DataFrame(forecasts, columns=fnames)
print(forecasts_df.iloc[:10,:])
print(forecasts_df.dtypes)

['_id', 'condate', 'day', 'date', 'code', 'low', 'high', 'text', 'creatat', 'changeat']
['_id', 'city', 'country', 'region', 'chill', 'direction', 'speed', 'sunrise', 'sunset', 'humidity', 'pressure', 'rising', 'visibility', 'pubdate', 'text', 'code', 'temperature', 'creatat', 'changeat']
Pocet forecasts: 36340
Pocet conditions: 3631
1
2020-01-18 19:00:00
Sat
2020-01-18 01:00:00
5
0
2
Rain And Snow
2020-01-18 20:15:13
2020-01-18 20:15:13
   _id              condate  day                 date  code  low  high  \
0    1  2020-01-18 19:00:00  Sat  2020-01-18 01:00:00     5    0     2   
1    2  2020-01-18 19:00:00  Sun  2020-01-19 01:00:00    28   -1     2   
2    3  2020-01-18 19:00:00  Mon  2020-01-20 01:00:00    28   -1     2   
3    4  2020-01-18 19:00:00  Tue  2020-01-21 01:00:00    32   -3     1   
4    5  2020-01-18 19:00:00  Wed  2020-01-22 01:00:00    28   -4     1   
5    6  2020-01-18 19:00:00  Thu  2020-01-23 01:00:00    30   -3     1   
6    7  2020-01-18 19:00:00  Fri  2020-0

In [20]:
columns = forecasts[0].keys()
row = forecasts[0]
dict(zip(columns,row))

{'_id': 1,
 'condate': '2020-01-18 19:00:00',
 'day': 'Sat',
 'date': '2020-01-18 01:00:00',
 'code': 5,
 'low': 0,
 'high': 2,
 'text': 'Rain And Snow',
 'creatat': '2020-01-18 20:15:13',
 'changeat': '2020-01-18 20:15:13'}

In [15]:
def json_data(a):
    #rows = readDB(a)
    rows = a
    columns = rows[0].keys()    # jmena sloupcu
    results = []
    for row in rows:
        results.append(dict(zip(columns,row)))
    return json.dumps(results)

In [16]:
json_data(forecasts)

'[{"_id": 1, "condate": "2020-01-18 19:00:00", "day": "Sat", "date": "2020-01-18 01:00:00", "code": 5, "low": 0, "high": 2, "text": "Rain And Snow", "creatat": "2020-01-18 20:15:13", "changeat": "2020-01-18 20:15:13"}, {"_id": 2, "condate": "2020-01-18 19:00:00", "day": "Sun", "date": "2020-01-19 01:00:00", "code": 28, "low": -1, "high": 2, "text": "Mostly Cloudy", "creatat": "2020-01-18 20:15:13", "changeat": "2020-01-18 20:15:13"}, {"_id": 3, "condate": "2020-01-18 19:00:00", "day": "Mon", "date": "2020-01-20 01:00:00", "code": 28, "low": -1, "high": 2, "text": "Mostly Cloudy", "creatat": "2020-01-18 20:15:13", "changeat": "2020-01-18 20:15:13"}, {"_id": 4, "condate": "2020-01-18 19:00:00", "day": "Tue", "date": "2020-01-21 01:00:00", "code": 32, "low": -3, "high": 1, "text": "Sunny", "creatat": "2020-01-18 20:15:13", "changeat": "2020-01-18 20:15:13"}, {"_id": 5, "condate": "2020-01-18 19:00:00", "day": "Wed", "date": "2020-01-22 01:00:00", "code": 28, "low": -4, "high": 1, "text": 